In [1]:
import pandas as pd
import numpy as np
import nltk
from nltk.tokenize import sent_tokenize, word_tokenize
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from nltk.tokenize import PunktSentenceTokenizer
from nltk.stem import SnowballStemmer, LancasterStemmer

In [2]:
df = pd.read_csv("dataset2.csv")
df.head()

slug  \
0  https://www.coffeereview.com/review/sweety-esp...   
1  https://www.coffeereview.com/review/flora-blen...   
2  https://www.coffeereview.com/review/ethiopia-s...   
3  https://www.coffeereview.com/review/ethiopia-s...   
4  https://www.coffeereview.com/review/ethiopia-g...   

                                            all_text  rating  \
0   \n\n\n95\n\n\nA.R.C.\n“Sweety” Espresso Blend...      95   
1   \n\n\n94\n\n\nA.R.C.\nFlora Blend Espresso\n\...      94   
2   \n\n\n92\n\n\nRevel Coffee\nEthiopia Shakiso ...      92   
3   \n\n\n92\n\n\nRoast House\nEthiopia Suke Quto...      92   
4   \n\n\n94\n\n\nBig Creek Coffee Roasters\nEthi...      94   

                     roaster                        name             location  \
0                     A.R.C.     “Sweety” Espresso Blend     Hong Kong, China   
1                     A.R.C.        Flora Blend Espresso     Hong Kong, China   
2               Revel Coffee    Ethiopia Shakiso Mormora    Billings, Montana   
3                Roast House          Ethiopia Suke Quto  Spokane, Washington   
4  Big Creek Coffee Roasters  Ethiopia Gedeb Halo Beriti    Hamilton, Montana   

                                             origin         roast  \
0                                  Panama; Ethiopia  Medium-Light   
1                              Africa; Asia Pacific  Medium-Light   
2                      Guji Zone, southern Ethiopia  Medium-Light   
3  Guji Zone, Oromia Region, south-central Ethiopia  Medium-Light   
4     Gedeb District, Gedeo Zone, southern Ethiopia        Medium   

            est_price    review_date  ... body  flavor  aftertaste  with_milk  \
0  HKD $250/227 grams  November 2017  ...  9.0     9.0         9.0        9.0   
1  HKD $158/227 grams  November 2017  ...  9.0     9.0         8.0        9.0   
2    $16.00/12 ounces  November 2017  ...  8.0     9.0         8.0        NaN   
3    $19.00/16 ounces  November 2017  ...  9.0     9.0         8.0        NaN   
4    $16.50/12 ounces  November 2017  ...  9.0     9.0         8.0        NaN   

                                              desc_1  \
0  Evaluated as espresso. Sweet-toned, deeply ric...   
1  Evaluated as espresso. Sweetly tart, floral-to...   
2  Crisply sweet, cocoa-toned. Lemon blossom, roa...   
3  Delicate, sweetly spice-toned. Pink peppercorn...   
4  Deeply sweet, subtly pungent. Honey, pear, tan...   

                                              desc_2  \
0  An espresso blend comprised of coffees from Pa...   
1  An espresso blend comprised of coffees from Af...   
2  This coffee tied for the third-highest rating ...   
3  This coffee tied for the third-highest rating ...   
4  Southern Ethiopia coffees like this one are pr...   

                                              desc_3  \
0  A radiant espresso blend that shines equally i...   
1  A floral-driven straight shot, amplified with ...   
2  A gently spice-toned, floral- driven wet-proce...   
3  Lavender-like flowers and hints of zesty pink ...   
4  A deeply and generously lush cup saved from se...   

                                        descriptions  \
0  Evaluated as espresso. Sweet-toned, deeply ric...   
1  Evaluated as espresso. Sweetly tart, floral-to...   
2  Crisply sweet, cocoa-toned. Lemon blossom, roa...   
3  Delicate, sweetly spice-toned. Pink peppercorn...   
4  Deeply sweet, subtly pungent. Honey, pear, tan...   

                                       relevant_text  latitude  
0  A.R.C.\n“Sweety” Espresso Blend\nHong Kong, Ch...  9.145000  
1  A.R.C.\nFlora Blend Espresso\nHong Kong, China... -8.783195  
2  Revel Coffee\nEthiopia Shakiso Mormora\nBillin...  6.515691  
3  Roast House\nEthiopia Suke Quto\nSpokane, Wash...  9.066516  
4  Big Creek Coffee Roasters\nEthiopia Gedeb Halo...  5.917024  

[5 rows x 23 columns]

In [3]:
tokens = [word_tokenize(i) for i in df["desc_1"]]
t1 = tokens[0]

In [4]:
t1

['Evaluated',
 'as',
 'espresso',
 '.',
 'Sweet-toned',
 ',',
 'deeply',
 'rich',
 ',',
 'chocolaty',
 '.',
 'Vanilla',
 'paste',
 ',',
 'dark',
 'chocolate',
 ',',
 'narcissus',
 ',',
 'pink',
 'grapefruit',
 'zest',
 ',',
 'black',
 'cherry',
 'in',
 'aroma',
 'and',
 'cup',
 '.',
 'Plush',
 ',',
 'syrupy',
 'mouthfeel',
 ';',
 'resonant',
 ',',
 'flavor-saturated',
 'finish',
 '.',
 'In',
 'three',
 'parts',
 'milk',
 ',',
 'rich',
 'chocolate',
 'tones',
 'intensify',
 ',',
 'along',
 'with',
 'intimations',
 'of',
 'vanilla',
 'paste',
 'and',
 'black',
 'cherry',
 'in',
 'the',
 'short',
 'finish',
 'and',
 'floral-toned',
 'citrus',
 'zest',
 'in',
 'the',
 'long',
 '.']

In [5]:
count = 0
for i in df["desc_1"]:
    if "three parts milk" in i:
        #print(i)
        count += 1
print(count)

210


In [6]:
def process_content(description):
    l = []
    try:
        words = nltk.word_tokenize(description.lower().replace("-"," "))
        #print(words)
        tagged = nltk.pos_tag(words)
        #print(tagged)

        # All chunks
        chunk_gram = r"""Chunk: {<NNP>?<RB.?>*<VBD>*<JJ.?>*<NNP.?>*<NN.?>*<NN.?>*}"""
        chunk_parser = nltk.RegexpParser(chunk_gram)
        chunked = chunk_parser.parse(tagged)

        # Finding the finish description
        finish_gram = r"""Chunk: {<NNP>?<RB.?>*<VBD>*<VBN>*<JJ.?>*<NNP.?>*<NN.?>*<NN.?>*<IN>+<DT>+<JJ.?>*<NN>*}"""
        finish_parser = nltk.RegexpParser(finish_gram)
        finish_chunks = finish_parser.parse(tagged)

        # Finding the milk description
        
        # print(description)

        for chunk in chunked:
            if hasattr(chunk,"label"):
                if chunk.label() == "Chunk":
                    l.append(chunk)
            # print(chunk)
        #print("---Finish---")
        if len(finish_chunks) == 0:
            for chunk in chunked:
                if hasattr(chunk,"label"):
                    if chunk.label() == "Chunk":
                        for j in chunk:
                            print(j[0])
        # for chunk in finish_chunks:
        #     if hasattr(chunk,"label"):
        #         if chunk.label() == "Chunk":
        #             print(chunk)
        #             # for j in chunk:
        #             #     print(j[0])
        #print("---Finish done---")

    except Exception as e:
        print(str(e))

    return l

chunks = process_content(df["desc_1"][0])
chunks

[Tree('Chunk', [('espresso', 'NN')]),
 Tree('Chunk', [('sweet', 'NN')]),
 Tree('Chunk', [('toned', 'VBD')]),
 Tree('Chunk', [('deeply', 'RB'), ('rich', 'JJ')]),
 Tree('Chunk', [('chocolaty', 'NN')]),
 Tree('Chunk', [('vanilla', 'NN'), ('paste', 'NN')]),
 Tree('Chunk', [('dark', 'JJ'), ('chocolate', 'NN')]),
 Tree('Chunk', [('narcissus', 'NN')]),
 Tree('Chunk', [('grapefruit', 'NN'), ('zest', 'NN')]),
 Tree('Chunk', [('black', 'JJ'), ('cherry', 'NN')]),
 Tree('Chunk', [('aroma', 'NN')]),
 Tree('Chunk', [('cup', 'NN')]),
 Tree('Chunk', [('plush', 'NN')]),
 Tree('Chunk', [('syrupy', 'JJ'), ('mouthfeel', 'NN')]),
 Tree('Chunk', [('resonant', 'NN')]),
 Tree('Chunk', [('flavor', 'NN')]),
 Tree('Chunk', [('saturated', 'VBD'), ('finish', 'JJ')]),
 Tree('Chunk', [('parts', 'NNS'), ('milk', 'NN')]),
 Tree('Chunk', [('rich', 'JJ'), ('chocolate', 'NN'), ('tones', 'NNS')]),
 Tree('Chunk', [('intimations', 'NNS')]),
 Tree('Chunk', [('vanilla', 'NN'), ('paste', 'NN')]),
 Tree('Chunk', [('black', 'JJ'

In [7]:
useless = ["milk","short","long","cup","flavor",
    "flavour","www","http","visit","information"
    "cafe","coffee","coffees","blend","shot"]

characteristic_names = ["finish","tone","tones","toned","mouthfeel","paste"
    "note","notes"]

def clean_chunk(chunk):
    grammar = [i[1] for i in chunk]
    words = [i[0] for i in chunk]
    for i in characteristic_names:
        for j in chunk:
            if j[0] == i:
                chunk.remove(j)
    for i in useless:
        if i in "".join(words):
            return None
    return chunk

In [8]:
clean = [clean_chunk(i) for i in chunks if clean_chunk(i) is not None]
clean

[Tree('Chunk', [('espresso', 'NN')]),
 Tree('Chunk', [('sweet', 'NN')]),
 Tree('Chunk', []),
 Tree('Chunk', [('deeply', 'RB'), ('rich', 'JJ')]),
 Tree('Chunk', [('chocolaty', 'NN')]),
 Tree('Chunk', [('vanilla', 'NN'), ('paste', 'NN')]),
 Tree('Chunk', [('dark', 'JJ'), ('chocolate', 'NN')]),
 Tree('Chunk', [('narcissus', 'NN')]),
 Tree('Chunk', [('grapefruit', 'NN'), ('zest', 'NN')]),
 Tree('Chunk', [('black', 'JJ'), ('cherry', 'NN')]),
 Tree('Chunk', [('aroma', 'NN')]),
 Tree('Chunk', [('plush', 'NN')]),
 Tree('Chunk', [('syrupy', 'JJ')]),
 Tree('Chunk', [('resonant', 'NN')]),
 Tree('Chunk', [('saturated', 'VBD')]),
 Tree('Chunk', [('rich', 'JJ'), ('chocolate', 'NN')]),
 Tree('Chunk', [('intimations', 'NNS')]),
 Tree('Chunk', [('vanilla', 'NN'), ('paste', 'NN')]),
 Tree('Chunk', [('black', 'JJ'), ('cherry', 'NN')]),
 Tree('Chunk', [('floral', 'JJ')]),
 Tree('Chunk', [('citrus', 'NN'), ('zest', 'NN')])]

In [9]:
stemmer = PorterStemmer()
stemmer = SnowballStemmer(language = "english")

In [10]:
def extract_characteristics(raw):
    characteristics = []
    for chunk in raw:
        grammar = [i[1] for i in chunk]
        words = [i[0] for i in chunk]
        clean = clean_chunk(chunk)
        if clean is None:
            continue

        if len(clean) == 0:
            continue
        
        if len(clean) == 1:
            if grammar[0] != "VBD":
                characteristics.append(stemmer.stem(words[0]))
            continue

        if all(i=="NN" for i in grammar):
            characteristics.append(stemmer.stem(words[0]))
            continue
        
        elif grammar[0].startswith('JJ') and grammar[1].startswith('NN'):
            characteristics.append(stemmer.stem(words[1]))
            continue

        elif grammar[0].startswith('RB') and grammar[1].startswith('JJ'):
            characteristics.append(stemmer.stem(words[1]))
            continue
    return np.array(characteristics)

extract_characteristics(chunks)

array(['espresso', 'sweet', 'rich', 'chocolati', 'vanilla', 'chocol',
       'narcissus', 'grapefruit', 'cherri', 'aroma', 'plush', 'syrupi',
       'reson', 'chocol', 'intim', 'vanilla', 'cherri', 'floral',
       'citrus'], dtype='<U10')

In [11]:
df["characteristics"] = df["desc_1"].apply(lambda x:extract_characteristics(process_content(x)))

In [12]:
df.head()

slug  \
0  https://www.coffeereview.com/review/sweety-esp...   
1  https://www.coffeereview.com/review/flora-blen...   
2  https://www.coffeereview.com/review/ethiopia-s...   
3  https://www.coffeereview.com/review/ethiopia-s...   
4  https://www.coffeereview.com/review/ethiopia-g...   

                                            all_text  rating  \
0   \n\n\n95\n\n\nA.R.C.\n“Sweety” Espresso Blend...      95   
1   \n\n\n94\n\n\nA.R.C.\nFlora Blend Espresso\n\...      94   
2   \n\n\n92\n\n\nRevel Coffee\nEthiopia Shakiso ...      92   
3   \n\n\n92\n\n\nRoast House\nEthiopia Suke Quto...      92   
4   \n\n\n94\n\n\nBig Creek Coffee Roasters\nEthi...      94   

                     roaster                        name             location  \
0                     A.R.C.     “Sweety” Espresso Blend     Hong Kong, China   
1                     A.R.C.        Flora Blend Espresso     Hong Kong, China   
2               Revel Coffee    Ethiopia Shakiso Mormora    Billings, Montana   
3                Roast House          Ethiopia Suke Quto  Spokane, Washington   
4  Big Creek Coffee Roasters  Ethiopia Gedeb Halo Beriti    Hamilton, Montana   

                                             origin         roast  \
0                                  Panama; Ethiopia  Medium-Light   
1                              Africa; Asia Pacific  Medium-Light   
2                      Guji Zone, southern Ethiopia  Medium-Light   
3  Guji Zone, Oromia Region, south-central Ethiopia  Medium-Light   
4     Gedeb District, Gedeo Zone, southern Ethiopia        Medium   

            est_price    review_date  ... flavor  aftertaste  with_milk  \
0  HKD $250/227 grams  November 2017  ...    9.0         9.0        9.0   
1  HKD $158/227 grams  November 2017  ...    9.0         8.0        9.0   
2    $16.00/12 ounces  November 2017  ...    9.0         8.0        NaN   
3    $19.00/16 ounces  November 2017  ...    9.0         8.0        NaN   
4    $16.50/12 ounces  November 2017  ...    9.0         8.0        NaN   

                                              desc_1  \
0  Evaluated as espresso. Sweet-toned, deeply ric...   
1  Evaluated as espresso. Sweetly tart, floral-to...   
2  Crisply sweet, cocoa-toned. Lemon blossom, roa...   
3  Delicate, sweetly spice-toned. Pink peppercorn...   
4  Deeply sweet, subtly pungent. Honey, pear, tan...   

                                              desc_2  \
0  An espresso blend comprised of coffees from Pa...   
1  An espresso blend comprised of coffees from Af...   
2  This coffee tied for the third-highest rating ...   
3  This coffee tied for the third-highest rating ...   
4  Southern Ethiopia coffees like this one are pr...   

                                              desc_3  \
0  A radiant espresso blend that shines equally i...   
1  A floral-driven straight shot, amplified with ...   
2  A gently spice-toned, floral- driven wet-proce...   
3  Lavender-like flowers and hints of zesty pink ...   
4  A deeply and generously lush cup saved from se...   

                                        descriptions  \
0  Evaluated as espresso. Sweet-toned, deeply ric...   
1  Evaluated as espresso. Sweetly tart, floral-to...   
2  Crisply sweet, cocoa-toned. Lemon blossom, roa...   
3  Delicate, sweetly spice-toned. Pink peppercorn...   
4  Deeply sweet, subtly pungent. Honey, pear, tan...   

                                       relevant_text  latitude  \
0  A.R.C.\n“Sweety” Espresso Blend\nHong Kong, Ch...  9.145000   
1  A.R.C.\nFlora Blend Espresso\nHong Kong, China... -8.783195   
2  Revel Coffee\nEthiopia Shakiso Mormora\nBillin...  6.515691   
3  Roast House\nEthiopia Suke Quto\nSpokane, Wash...  9.066516   
4  Big Creek Coffee Roasters\nEthiopia Gedeb Halo...  5.917024   

                                     characteristics  
0  [espresso, sweet, rich, chocolati, vanilla, ch...  
1  [espresso, floral, honeysuckl, oak, chocol, th...  
2  [crispli, cocoa, blossom, date, rice, pepperco...  
3  [deli

In [13]:
all_characteristics = set([])
for i in df["characteristics"]:
    all_characteristics.update(i)

all_characteristics

{'access',
 'acid',
 'acrid',
 'addit',
 'adult',
 'agav',
 'akin',
 'alcohol',
 'aliv',
 'all',
 'allspic',
 'almond',
 'almondi',
 'almost',
 'aloewood',
 'also',
 'alyssum',
 'amber',
 'amond',
 'amplif',
 'amplifi',
 'anchor',
 'anis',
 'appeal',
 'appear',
 'appl',
 'apricot',
 'aprium',
 'aroma',
 'aromat',
 'array',
 'assess',
 'attract',
 'author',
 'autumn',
 'azalea',
 'back',
 'backdrop',
 'background',
 'bacon',
 'bake',
 'baker',
 'balanc',
 'ballast',
 'balm',
 'balsa',
 'banana',
 'barley',
 'barrel',
 'base',
 'bay',
 'bean',
 'beauti',
 'beef',
 'bergamot',
 'berri',
 'beverag',
 'big',
 'bight',
 'bing',
 'bit',
 'bitter',
 'bitter/tart',
 'bitterish',
 'bittersweet',
 'bizarr',
 'blackberri',
 'blackcurr',
 'blood',
 'bloom',
 'blossom',
 'blueberri',
 'bodi',
 'bold',
 'bosc',
 'bottom',
 'bouquet',
 'bourbon',
 'boysenberri',
 'brace',
 'brandi',
 'brazil',
 'breadfruit',
 'brew',
 'bright',
 'brilliant',
 'brisk',
 'brittl',
 'brothi',
 'brown',
 'bubblegum',
 'bu

In [14]:
df["coffee"] = df["name"] + "-" + df["roaster"]
df.head(3)

slug  \
0  https://www.coffeereview.com/review/sweety-esp...   
1  https://www.coffeereview.com/review/flora-blen...   
2  https://www.coffeereview.com/review/ethiopia-s...   

                                            all_text  rating       roaster  \
0   \n\n\n95\n\n\nA.R.C.\n“Sweety” Espresso Blend...      95        A.R.C.   
1   \n\n\n94\n\n\nA.R.C.\nFlora Blend Espresso\n\...      94        A.R.C.   
2   \n\n\n92\n\n\nRevel Coffee\nEthiopia Shakiso ...      92  Revel Coffee   

                       name           location                        origin  \
0   “Sweety” Espresso Blend   Hong Kong, China              Panama; Ethiopia   
1      Flora Blend Espresso   Hong Kong, China          Africa; Asia Pacific   
2  Ethiopia Shakiso Mormora  Billings, Montana  Guji Zone, southern Ethiopia   

          roast           est_price    review_date  ... aftertaste  with_milk  \
0  Medium-Light  HKD $250/227 grams  November 2017  ...        9.0        9.0   
1  Medium-Light  HKD $158/227 grams  November 2017  ...        8.0        9.0   
2  Medium-Light    $16.00/12 ounces  November 2017  ...        8.0        NaN   

                                              desc_1  \
0  Evaluated as espresso. Sweet-toned, deeply ric...   
1  Evaluated as espresso. Sweetly tart, floral-to...   
2  Crisply sweet, cocoa-toned. Lemon blossom, roa...   

                                              desc_2  \
0  An espresso blend comprised of coffees from Pa...   
1  An espresso blend comprised of coffees from Af...   
2  This coffee tied for the third-highest rating ...   

                                              desc_3  \
0  A radiant espresso blend that shines equally i...   
1  A floral-driven straight shot, amplified with ...   
2  A gently spice-toned, floral- driven wet-proce...   

                                        descriptions  \
0  Evaluated as espresso. Sweet-toned, deeply ric...   
1  Evaluated as espresso. Sweetly tart, floral-to...   
2  Crisply sweet, cocoa-toned. Lemon blossom, roa...   

                                       relevant_text  latitude  \
0  A.R.C.\n“Sweety” Espresso Blend\nHong Kong, Ch...  9.145000   
1  A.R.C.\nFlora Blend Espresso\nHong Kong, China... -8.783195   
2  Revel Coffee\nEthiopia Shakiso Mormora\nBillin...  6.515691   

                                     characteristics  \
0  [espresso, sweet, rich, chocolati, vanilla, ch...   
1  [espresso, floral, honeysuckl, oak, chocol, th...   
2  [crispli, cocoa, blossom, date, rice, pepperco...   

                                  coffee  
0         “Sweety” Espresso Blend-A.R.C.  
1            Flora Blend Espresso-A.R.C.  
2  Ethiopia Shakiso Mormora-Revel Coffee  

[3 rows x 25 columns]

In [15]:
# We want to remove characteristics that appear in less that 10% of the coffees
d = {}
for i in df["characteristics"]:
    for j in i:
        if j in d:
            d[j] += 1
        else:
            d[j] = 1

count_dict = {i:j for i,j in d.items() if j > len(df)/10}
count_dict

{'espresso': 315,
 'sweet': 1195,
 'rich': 415,
 'chocolati': 398,
 'chocol': 1558,
 'narcissus': 256,
 'cherri': 238,
 'aroma': 2255,
 'plush': 309,
 'syrupi': 536,
 'reson': 279,
 'floral': 487,
 'oak': 235,
 'gentl': 373,
 'crispli': 244,
 'cocoa': 1070,
 'delic': 230,
 'finish': 511,
 'hint': 433,
 'crisp': 536,
 'acid': 1239,
 'zest': 334,
 'juici': 553,
 'structur': 691,
 'almond': 579,
 'sandalwood': 340,
 'fruit': 435,
 'high': 271,
 'apricot': 267,
 'magnolia': 291,
 'savori': 265,
 'full': 514,
 'cedar': 761,
 'cut': 317,
 'tart': 468,
 'hazelnut': 358,
 'satini': 354,
 'flower': 351,
 'underton': 256,
 'velveti': 293,
 'bright': 376}

In [16]:
one_hot = pd.DataFrame(columns = ["coffee"] + list(count_dict.keys()))
one_hot

Empty DataFrame
Columns: [coffee, espresso, sweet, rich, chocolati, chocol, narcissus, cherri, aroma, plush, syrupi, reson, floral, oak, gentl, crispli, cocoa, delic, finish, hint, crisp, acid, zest, juici, structur, almond, sandalwood, fruit, high, apricot, magnolia, savori, full, cedar, cut, tart, hazelnut, satini, flower, underton, velveti, bright]
Index: []

[0 rows x 42 columns]

In [17]:
d = {"coffee":df["coffee"]}

for i in count_dict.keys():
    d[i] = df["characteristics"].apply(lambda x: 0 if i in x else 1)

In [18]:
one_hot = pd.DataFrame(d)
one_hot.head()

coffee  espresso  sweet  rich  \
0                     “Sweety” Espresso Blend-A.R.C.         0      0     0   
1                        Flora Blend Espresso-A.R.C.         0      1     1   
2              Ethiopia Shakiso Mormora-Revel Coffee         1      1     0   
3                     Ethiopia Suke Quto-Roast House         1      1     1   
4  Ethiopia Gedeb Halo Beriti-Big Creek Coffee Ro...         1      0     1   

   chocolati  chocol  narcissus  cherri  aroma  plush  ...  full  cedar  cut  \
0          0       0          0       0      0      0  ...     1      1    1   
1          1       0          1       1      0      1  ...     1      1    1   
2          1       1          1       1      0      1  ...     1      1    1   
3          1       1          1       1      0      1  ...     1      1    1   
4          1       0          1       1      0      0  ...     1      1    1   

   tart  hazelnut  satini  flower  underton  velveti  bright  
0     1         1       1       1         1        1       1  
1     1         1       1       1         1        1       1  
2     1         1       1       1         1        1       1  
3     1         1       1       1         1        1       1  
4     1         1       1       1         1        1       1  

[5 rows x 42 columns]

In [19]:
from sklearn.neighbors import NearestNeighbors

In [20]:
one_hot[one_hot.columns[1:]]

espresso  sweet  rich  chocolati  chocol  narcissus  cherri  aroma  \
0            0      0     0          0       0          0       0      0   
1            0      1     1          1       0          1       1      0   
2            1      1     0          1       1          1       1      0   
3            1      1     1          1       1          1       1      0   
4            1      0     1          1       0          1       1      0   
...        ...    ...   ...        ...     ...        ...     ...    ...   
2277         1      1     1          1       0          1       1      0   
2278         1      1     1          0       1          1       1      0   
2279         1      0     1          1       1          0       0      0   
2280         1      0     1          0       0          1       1      0   
2281         0      1     1          1       0          1       1      0   

      plush  syrupi  ...  full  cedar  cut  tart  hazelnut  satini  flower  \
0         0       0  ...     1      1    1     1         1       1       1   
1         1       0  ...     1      1    1     1         1       1       1   
2         1       1  ...     1      1    1     1         1       1       1   
3         1       1  ...     1      1    1     1         1       1       1   
4         0       1  ...     1      1    1     1         1       1       1   
...     ...     ...  ...   ...    ...  ...   ...       ...     ...     ...   
2277      1       0  ...     1      1    1     1         1       1       1   
2278      1       1  ...     1      0    1     1         1       1       1   
2279      1       1  ...     1      1    1     1         1       1       1   
2280      1       0  ...     1      1    1     0         0       1       1   
2281      1       0  ...     1      0    1     1         0       1       1   

      underton  velveti  bright  
0            1        1       1  
1            1        1       1  
2            1        1       1  
3            1        1       1  
4            1        1       1  
...        ...      ...     ...  
2277         1        1       1  
2278         1        1       1  
2279         1        1       1  
2280         1        1       1  
2281         1        1       1  

[2282 rows x 41 columns]

In [21]:
X = one_hot[one_hot.columns[1:]]
nbrs = NearestNeighbors(n_neighbors=6, algorithm='ball_tree').fit(X)
distances, indices = nbrs.kneighbors(X)

In [22]:
import prince

In [23]:
# We want to reduce the number of features but limit the difference in nearest neighbours
# We stop once only 10% of the sets have no overlap
l = [0]
n = 4
while True:
    n+=1
    mca = prince.MCA(n_components=n)
    mca = mca.fit(X)
    mca = mca.transform(X)
    nbrs = NearestNeighbors(n_neighbors=6, algorithm='ball_tree').fit(mca)
    mca_distances, mca_indices = nbrs.kneighbors(mca)
    l = []
    for i in range(len(indices)):
        l.append(len(set(indices[i][1:]) & set(mca_indices[i][1:])))
    if l.count(0) < len(l)/10:
        break
print(n)

20


In [24]:
mca = prince.MCA(n_components=n)
mca = mca.fit(X)
mca = mca.transform(X)
mca

0         1         2         3         4         5         6   \
0    -0.025074  0.318228  0.047341  0.123570  0.224134 -0.073037 -0.137453   
1    -0.021282  0.241927 -0.002136 -0.087406  0.057331  0.019256 -0.087875   
2    -0.023370 -0.031865  0.161014 -0.097921 -0.095761  0.092606 -0.029032   
3    -0.026508 -0.088908 -0.047582 -0.105501 -0.107253 -0.014130 -0.076721   
4    -0.012232  0.137956  0.082171  0.214607  0.128401  0.168808 -0.021614   
...        ...       ...       ...       ...       ...       ...       ...   
2277 -0.035554 -0.028238 -0.215958 -0.107268  0.085084  0.165797  0.070560   
2278 -0.029716 -0.125359 -0.049122 -0.087392 -0.142736  0.106244  0.070983   
2279 -0.032637 -0.114409 -0.031698  0.096874 -0.044234 -0.132988 -0.083686   
2280 -0.029880  0.020770 -0.158768  0.072235  0.176584 -0.140756 -0.062827   
2281 -0.021416  0.255331 -0.004244 -0.081082  0.047578 -0.073518  0.080293   

            7         8         9         10            11        12  \
0     0.100728 -0.154277  0.011980  0.082145 -1.591995e-01  0.054948   
1     0.129130 -0.052712  0.005751  0.049171 -8.144220e-02  0.054733   
2     0.116825  0.046812 -0.205092  0.035975 -6.747499e-02 -0.058234   
3    -0.052736 -0.013819  0.045564  0.082186  5.669823e-02 -0.056458   
4    -0.127139 -0.045679 -0.059762 -0.028724  1.076397e-07 -0.064673   
...        ...       ...       ...       ...           ...       ...   
2277  0.010055 -0.008364 -0.034441  0.158414 -9.949816e-03  0.138133   
2278  0.044178 -0.137399  0.119198 -0.104354 -1.903276e-01  0.044232   
2279 -0.056406  0.000120  0.088082  0.084780  4.667258e-02 -0.049794   
2280 -0.058448 -0.044814 -0.034318  0.003095  6.344402e-02 -0.018752   
2281  0.084509 -0.122866 -0.035789 -0.021318 -9.312711e-03 -0.095518   

            13        14        15        16        17        18        19  
0     0.100231  0.130608  0.074157 -0.055955  0.024163  0.004772  0.021922  
1     0.069691 -0.029135  0.076557 -0.049521 -0.045076 -0.061630 -0.007245  
2    -0.050596  0.068040 -0.110130 -0.086570  0.064054  0.039209 -0.065462  
3    -0.011289  0.023476  0.011826  0.008833 -0.021977  0.008797  0.002627  
4    -0.023350 -0.032725 -0.096161  0.013103 -0.096367 -0.121343 -0.037638  
...        ...       ...       ...       ...       ...       ...       ...  
2277 -0.063064 -0.109777 -0.015794  0.022110  0.058432 -0.060490 -0.047792  
2278  0.002513 -0.090134 -0.094571 -0.101859  0.005061 -0.033791 -0.089631  
2279  0.029132  0.004829 -0.001622 -0.005800 -0.054665  0.017048  0.058673  
2280 -0.059419 -0.000444  0.106879 -0.107217  0.071196 -0.079655 -0.046382  
2281  0.013086 -0.073156  0.065811  0.097957  0.081619  0.028383 -0.030290  

[2282 rows x 20 columns]

In [25]:
df["recommendations"] = [i[1:] for i in mca_indices]
df["string_recommendation"] = [[df["name"][j] for j in i[1:]] for i in mca_indices]
for i in df["string_recommendation"][0:3]:
    print(i)

['D31 The New Life', 'Indonesia Sumatra Gayo Espresso', 'Zoom Espresso', 'Ethiopia Guji Uraga More Floral Kudume Washed', 'Kenya AA Ares Phoenix Special']
['Flight Seasonal Espresso', 'Ethiopia Gotiti Natural', 'Mama Cata Mokkita', 'Zoom Espresso', 'Chasing Horizon Natural Espresso']
['Estelí Nicaragua', 'Ethiopia Natural Guji Blue-Donkey 2020', 'Crescent Blend', 'Gigesa Ethiopia', 'Yemen Mocha Haimi']


In [26]:
df.rename(columns={"desc_1":"description"},inplace=True)

In [27]:
df.head(3)

slug  \
0  https://www.coffeereview.com/review/sweety-esp...   
1  https://www.coffeereview.com/review/flora-blen...   
2  https://www.coffeereview.com/review/ethiopia-s...   

                                            all_text  rating       roaster  \
0   \n\n\n95\n\n\nA.R.C.\n“Sweety” Espresso Blend...      95        A.R.C.   
1   \n\n\n94\n\n\nA.R.C.\nFlora Blend Espresso\n\...      94        A.R.C.   
2   \n\n\n92\n\n\nRevel Coffee\nEthiopia Shakiso ...      92  Revel Coffee   

                       name           location                        origin  \
0   “Sweety” Espresso Blend   Hong Kong, China              Panama; Ethiopia   
1      Flora Blend Espresso   Hong Kong, China          Africa; Asia Pacific   
2  Ethiopia Shakiso Mormora  Billings, Montana  Guji Zone, southern Ethiopia   

          roast           est_price    review_date  ...  \
0  Medium-Light  HKD $250/227 grams  November 2017  ...   
1  Medium-Light  HKD $158/227 grams  November 2017  ...   
2  Medium-Light    $16.00/12 ounces  November 2017  ...   

                                         description  \
0  Evaluated as espresso. Sweet-toned, deeply ric...   
1  Evaluated as espresso. Sweetly tart, floral-to...   
2  Crisply sweet, cocoa-toned. Lemon blossom, roa...   

                                              desc_2  \
0  An espresso blend comprised of coffees from Pa...   
1  An espresso blend comprised of coffees from Af...   
2  This coffee tied for the third-highest rating ...   

                                              desc_3  \
0  A radiant espresso blend that shines equally i...   
1  A floral-driven straight shot, amplified with ...   
2  A gently spice-toned, floral- driven wet-proce...   

                                        descriptions  \
0  Evaluated as espresso. Sweet-toned, deeply ric...   
1  Evaluated as espresso. Sweetly tart, floral-to...   
2  Crisply sweet, cocoa-toned. Lemon blossom, roa...   

                                       relevant_text  latitude  \
0  A.R.C.\n“Sweety” Espresso Blend\nHong Kong, Ch...  9.145000   
1  A.R.C.\nFlora Blend Espresso\nHong Kong, China... -8.783195   
2  Revel Coffee\nEthiopia Shakiso Mormora\nBillin...  6.515691   

                                     characteristics  \
0  [espresso, sweet, rich, chocolati, vanilla, ch...   
1  [espresso, floral, honeysuckl, oak, chocol, th...   
2  [crispli, cocoa, blossom, date, rice, pepperco...   

                                  coffee                recommendations  \
0         “Sweety” Espresso Blend-A.R.C.    [635, 657, 809, 2189, 1127]   
1            Flora Blend Espresso-A.R.C.   [1354, 266, 1740, 809, 2037]   
2  Ethiopia Shakiso Mormora-Revel Coffee  [992, 1148, 1031, 1576, 1502]   

                               string_recommendation  
0  [D31 The New Life, Indonesia Sumatra Gayo Espr...  
1  [Flight Seasonal Espresso, Ethiopia Gotiti Nat...  
2  [Estelí Nicaragua, Ethiopia Natural Guji Blue-...  

[3 rows x 27 columns]

In [28]:
import pickle
with open("data.p","wb") as f:
    pickle.dump(df,f)

In [29]:
data_dict = df.to_dict("index")
import pickle
with open("data.p","wb") as f:
    pickle.dump(data_dict,f)

In [30]:
data_dict

{0: {'slug': 'https://www.coffeereview.com/review/sweety-espresso-blend/',
  'all_text': ' \n\n\n95\n\n\nA.R.C.\n“Sweety” Espresso Blend\n\n\n\n\n\n\n\n\nRoaster Location:\nHong Kong, China\n\n\nCoffee Origin:\nPanama; Ethiopia\n\n\nRoast Level:\nMedium-Light\n\n\nAgtron:\n50/73\n\n\nEst. Price:\nHKD $250/227 grams\n\n\n\n\n\n\nReview Date:\nNovember 2017\n\n\nAroma:\n9\n\n\nBody:\n9\t\t\t\t\t\t\t\n\nFlavor:\n9\n\n\nAftertaste:\n9\n\n\nWith Milk:\n9\n\n\n\n\nBlind Assessment: Evaluated as espresso. Sweet-toned, deeply rich, chocolaty. Vanilla paste, dark chocolate, narcissus, pink grapefruit zest, black cherry in aroma and cup. Plush, syrupy mouthfeel; resonant, flavor-saturated finish. In three parts milk, rich chocolate tones intensify, along with intimations of vanilla paste and black cherry in the short finish and floral-toned citrus zest in the long. \nNotes: An espresso blend comprised of coffees from Panama and Ethiopia. A.R.C., whose motto is “more than specialty,” rigorously c

In [31]:
for i in df["roaster"]:
    print(i)

A.R.C.
A.R.C.
Revel Coffee
Roast House
Big Creek Coffee Roasters
Red Rooster Coffee Roaster
Willoughby's Coffee & Tea
Black Oak Coffee Roasters
Wonderstate Coffee
Reunion Island Coffee
PT's Coffee Roasting
Kakalove Cafe
Level Ground Trading
Old Soul Co.
A.R.C.
A.R.C.
A.R.C.
A.R.C.
A.R.C.
A.R.C.
A.R.C.
A.R.C.
Bootstrap Coffee Roasters
Paradise Roasters
Glory Brew
Hula Daddy Kona Coffee
Kakalove Cafe
Jackrabbit Java
Kakalove Cafe
Propeller Coffee
Propeller Coffee
Propeller Coffee
Chocolate Fish Coffee Roasters
Caffe Luxxe
Espresso Republic
Lexington Coffee Roasters
Big Creek Coffee Roasters
Mystic Monk Coffee
Mystic Monk Coffee
Noble Coffee Roasting
Red E Café
Ben's Beans
Espresso Republic
Cimarron Coffee Roasters
Roast House
Red Rooster Coffee Roaster
Speckled Ax
Fumi Coffee
Good Folks Coffee
Flight Coffee Co.
Dragonfly Coffee Roasters
OQ Coffee Co.
Green Stone Coffee
Willoughby's Coffee & Tea
Bird Rock Coffee Roasters
Equator Coffees & Teas
JBC Coffee Roasters
Willoughby's Coffee & Tea

In [32]:
df.columns

Index(['slug', 'all_text', 'rating', 'roaster', 'name', 'location', 'origin',
       'roast', 'est_price', 'review_date', 'agtron', 'aroma', 'acid', 'body',
       'flavor', 'aftertaste', 'with_milk', 'description', 'desc_2', 'desc_3',
       'descriptions', 'relevant_text', 'latitude', 'characteristics',
       'coffee', 'recommendations', 'string_recommendation'],
      dtype='object')

In [40]:
d = {value["name"]:key for key,value in data_dict.items()}

In [41]:
with open("keys.p","wb") as f:
    pickle.dump(d,f)

In [44]:
d

{'“Sweety” Espresso Blend': 0,
 'Flora Blend Espresso': 1,
 'Ethiopia Shakiso Mormora': 2,
 'Ethiopia Suke Quto': 1312,
 'Ethiopia Gedeb Halo Beriti': 4,
 'Ethiopia Kayon Mountain': 2160,
 'Ethiopia Gelgelu Natural Organic': 6,
 'Ethiopia Hambela Alaka': 470,
 'Organic Ethiopia Kirite': 8,
 'Ethiopia Sidama': 2139,
 'Thiriku AA Kenya': 10,
 'Ethiopia Natural Yirgacheffe Tore': 11,
 'Direct Fair Trade Espresso': 12,
 'Decaf Ethiopia Sidamo': 13,
 '“Flowery” Espresso Blend': 14,
 '“Chocolate” Espresso Blend': 15,
 '“Nutty” Espresso Blend': 16,
 'Ethiopia Yirgacheffe Washed G1': 17,
 '“Blue Mountain Flavor” Blend': 18,
 'House Blend Espresso': 19,
 'Ethiopia Yirgacheffe Natural G1': 20,
 '“Fruity” Espresso Blend': 21,
 'Decaf Colombia Select': 22,
 'Ethiopia Awassa': 23,
 'The Knight Dark Roast': 24,
 '100% Kona SL-28': 25,
 'Kenya Kirinyaga Mukangu AB': 194,
 'Kenya Nyeri Othaya Gatugi Red Cherry Project AA': 27,
 'Ethiopia Washed Yirgacheffe Adado': 28,
 'Outbound Espresso': 29,
 'Ace E